In [1]:
!git clone https://github.com/huggingface/diffusers
%cd diffusers
!pip install .
%cd examples/text_to_image
!pip install -r requirements.txt


Cloning into 'diffusers'...
remote: Enumerating objects: 84298, done.
remote: Counting objects: 100% (1040/1040), done.
remote: Compressing objects: 100% (510/510), done.
remote: Total 84298 (delta 874), reused 535 (delta 525), pack-reused 83258 (from 5)
Receiving objects: 100% (84298/84298), 62.08 MiB | 18.49 MiB/s, done.
Resolving deltas: 100% (61688/61688), done.
/diffusers


/venv/main/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


Processing /diffusers
  Installing build dependencies ... one
doneGetting requirements to build wheel ... 
donePreparing metadata (pyproject.toml) ... 
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 KB 9.2 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 781.7/781.7 KB 15.5 MB/s eta 0:00:00a 0:00:01
doneel for diffusers (pyproject.toml) ... 
  Created wheel for diffusers: filename=diffusers-0.33.0.dev0-py3-none-any.whl size=3492578 sha256=44980f25a168e00b2ea28afa59596529238946ac9213aaa02d2db787ac5c9f60
  Stored in directory: /tmp/pip-ephem-wheel-cache-egyt65nf/wheels/ef/1d/18/63f173880522d35ab033a67241c96d31aa93feb1e83d6df67d
Successfully built diffusers
/diffusers/examples/text_to_image
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 345.1/345.1 KB 11.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 83.5 MB/s eta 0:00:0000:010:01m
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 487.4/487.4 KB 34.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

In [3]:
!accelerate config default



accelerate configuration saved at /root/.cache/huggingface/accelerate/default_config.yaml


In [4]:
!pip install datasets


In [5]:
from datasets import load_dataset

dataset = load_dataset("lambdalabs/naruto-blip-captions", split="train")
print(dataset)


README.md:   0%|          | 0.00/1.02k [00:00<?, ?B/s]

Repo card metadata block was not found. Setting CardData to empty.


dataset_infos.json:   0%|          | 0.00/897 [00:00<?, ?B/s]

(…)-00000-of-00002-12944970063701d5.parquet:   0%|          | 0.00/344M [00:00<?, ?B/s]

(…)-00001-of-00002-cefa2f480689f147.parquet:   0%|          | 0.00/357M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/1221 [00:00<?, ? examples/s]

Dataset({
    features: ['image', 'text'],
    num_rows: 1221
})


In [6]:
!export dataset_name="lambdalabs/naruto-blip-captions"


In [8]:
%%bash
export MODEL_NAME="CompVis/stable-diffusion-v1-4"
export OUTPUT_DIR="sd-naruto-model"

accelerate launch train_text_to_image.py \
  --pretrained_model_name_or_path=$MODEL_NAME \
  --dataset_name="lambdalabs/naruto-blip-captions" \
  --use_ema \
  --resolution=512 --center_crop --random_flip \
  --train_batch_size=1 \
  --gradient_accumulation_steps=4 \
  --gradient_checkpointing \
  --mixed_precision="fp16" \
  --max_train_steps=150 \
  --learning_rate=1e-05 \
  --max_grad_norm=1 \
  --lr_scheduler="constant" \
  --lr_warmup_steps=0 \
  --output_dir=$OUTPUT_DIR


03/16/2025 03:54:26 - INFO - __main__ - Distributed environment: NO
Num processes: 1
0rocess index: 
Local process index: 0
Device: cuda

Mixed precision type: fp16

{'variance_type', 'dynamic_thresholding_ratio', 'clip_sample_range', 'timestep_spacing', 'thresholding', 'rescale_betas_zero_snr', 'sample_max_value', 'prediction_type'} was not found in config. Values will be initialized to default values.
Instantiating AutoencoderKL model under default dtype torch.float32.
{'mid_block_add_attention', 'latents_mean', 'latents_std', 'norm_num_groups', 'use_post_quant_conv', 'force_upcast', 'shift_factor', 'use_quant_conv'} was not found in config. Values will be initialized to default values.
All model checkpoint weights were used when initializing AutoencoderKL.

derKL were initialized from the model checkpoint at CompVis/stable-diffusion-v1-4.
imilar to the task the model of the checkpoint was trained on, you can already use AutoencoderKL for predictions without further training.
Instant

In [ ]:
from diffusers import StableDiffusionPipeline
import torch
from IPython.display import display

# Load the fine-tuned model from your output directory
pipe = StableDiffusionPipeline.from_pretrained("sd-naruto-model", torch_dtype=torch.float16)
pipe = pipe.to("cuda")

# Define your text prompt
prompt = "A guy playing a guitar"

# Generate an image from the prompt
image = pipe(prompt).images[0]

# Save the generated image
image.save("inference_output.png")

# Display the image inline
display(image)
